In [1]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.neighbors import NearestNeighbors

# Load the data
data = pd.read_csv("data.csv")

cols = data.columns
cols = cols[:-1]
print(cols)

df = data.iloc[:, :-1].astype(str)
print(df.head())

Index(['blackheads', 'cysts', 'inflammation', 'nodules', 'papules', 'pustules',
       'redness', 'whiteheads', 'coughing', 'fatigue',
       ...
       'rectal_pain', 'strong_urge_to_urinate', 'strong_smelling_urine',
       'red_eyes', 'male', 'female', 'infant', 'child', 'adult', 'senior'],
      dtype='object', length=632)
  blackheads cysts inflammation nodules papules pustules redness whiteheads  \
0          1     1            1       1       1        1       1          1   
1          1     1            1       1       1        1       1          1   
2          1     1            1       1       1        1       1          1   
3          1     1            1       1       1        1       1          1   
4          0     0            0       0       0        0       0          0   

  coughing fatigue  ... rectal_pain strong_urge_to_urinate  \
0        0       0  ...           0                      0   
1        0       0  ...           0                      0   
2        0

In [2]:
# data analysis
print(df.info())

print(df.describe())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 630 entries, 0 to 629
Columns: 632 entries, blackheads to senior
dtypes: object(632)
memory usage: 3.0+ MB
None
       blackheads cysts inflammation nodules papules pustules redness  \
count         630   630          630     630     630      630     630   
unique          2     2            2       2       2        2       2   
top             0     0            0       0       0        0       0   
freq          626   626          626     626     626      626     609   

       whiteheads coughing fatigue  ... rectal_pain strong_urge_to_urinate  \
count         630      630     630  ...         630                    630   
unique          2        2       2  ...           2                      2   
top             0        0       0  ...           0                      0   
freq          626      608     364  ...         624                    624   

       strong_smelling_urine red_eyes male female infant child adult senior  
cou

In [3]:
import matplotlib.pyplot as plt
plt.figure(figsize=(90, 50))

category_counts = data['disease'].value_counts()


plt.pie(category_counts, labels=category_counts.index,  autopct='%1.1f%%', shadow=True, startangle=90)

plt.title('Distribution', fontsize=16, fontweight='bold')
plt.legend(category_counts.index, loc='best', fontsize=50)
plt.axis('equal')

plt.show()

In [4]:
input_age = 'adult'
input_gender = 'male'
input_symptoms = ['blackheads', 'cysts', 'inflammation', 'nodules']

In [5]:
# process the data to get the list of symptoms
docs = []
filter_df = []
for i in range(len(df)):
    item = []
    for j in range(len(cols)):
        if df.iloc[i][j] == '1':
            item.append(cols[j])
    if(item[-1] == input_age and item[-2] == input_gender):
        docs.append(','.join(item[:-2]))
        filter_df.append(data.iloc[i]['disease'])
    
print(docs)
print(filter_df)

['blackheads,cysts,inflammation,nodules,papules,pustules,redness,whiteheads', 'coughing,fatigue,headache,itchy_eyes,itchy_nose,itchy_throat,nasal_congestion,runny_nose,sneezing,watery_eyes', 'difficulty_swallowing,difficulty_with_coordination,difficulty_with_balance,muscle_cramps,muscel_twitching,muscle_weakness,progressive_paralysis,slurred_speech', 'fatigue,headache,cold_hands,cold_feet,dizziness,irregular_heartbeat,lightheadedness,pale_skin,yellowish_skin,shortness_of_breath,weakness', 'difficulty_concentrating,feeling_nervous,feeling_weak,having_sense_of_panic,increased_heart_rate,rapid_breathing,restless,sweating,tense,present_worry_distraction,tired,trembling', 'fatigue,difficulty_concentrating,excessive_worry,irritability,muscle_tension,panic_attacks,restlessness,sleep_disturbances', 'redness,fatigue,decreased_range_of_motion,fever,joint_pain,stiffness,swelling,weight_loss', 'coughing,shortness_of_breath,chest_tightness,wheezing', 'brown_scar_like_lesion,crusting,oozing,open_sor

In [6]:
# instantiate CountVectorizer() 
cv=CountVectorizer() 

# this steps generates word counts for the words in your docs 
word_count_vector=cv.fit_transform(docs)

word_count_vector.shape

(97, 478)

In [7]:
# compute the itf values
tfidf_transformer = TfidfTransformer(smooth_idf=True,use_idf=True) 
tfidf_transformer.fit(word_count_vector)

# print idf values 
idf_values = tfidf_transformer.idf_
idf_values_log = np.log(idf_values)

df_idf = pd.DataFrame(idf_values_log, index=cv.get_feature_names_out(), columns=["idf_weights"])

# sort
df_idf.sort_values(by=['idf_weights'])

idf_weights
fatigue                                0.613724
fever                                  0.781053
nausea                                 0.951363
vomiting                               1.056719
headache                               1.105263
...                                         ...
itchy_eyes                             1.587564
itchy_blisters                         1.587564
itching_sensation                      1.587564
burning_sensation_in_upper_abdomen     1.587564
loss_of_memory                         1.587564

[478 rows x 1 columns]

In [8]:
# K Nearest Neighbors
k = 5 
knn_model = NearestNeighbors(n_neighbors=k, algorithm='brute', metric='cosine')
knn_model.fit(word_count_vector)

NearestNeighbors(algorithm='brute', metric='cosine')

In [13]:
# find the top k diseases
input_vector = cv.transform(input_symptoms)
distances, indices = knn_model.kneighbors(input_vector, n_neighbors=5)
print(distances[0])

# Get the top diseases
top_diseases = [filter_df[i] for i in indices[0]]

pd.DataFrame(top_diseases)

[0.64644661 1.         1.         1.         1.        ]


0
0                acne
1  multiple_sclerosis
2            migraine
3   myasthenia_gravis
4               mumps

In [14]:
all_symptoms = []
for i in indices[0]:
    symp = docs[i].split(',')
    all_symptoms += [s for s in symp if s not in input_symptoms]

In [11]:
#instantiate CountVectorizer() 
new_cv=CountVectorizer() 

# this steps generates word counts for the words in your docs 
new_word_count_vector=new_cv.fit_transform(all_symptoms)

new_word_count_vector.shape

# compute the itf values
new_tfidf_transformer = TfidfTransformer(smooth_idf=True,use_idf=True)
new_tfidf_transformer.fit(new_word_count_vector)

# print idf values
new_idf_values = new_tfidf_transformer.idf_
new_idf_values_log = np.log(new_idf_values)

new_df_idf = pd.DataFrame(new_idf_values_log, index=new_cv.get_feature_names_out(), columns=["idf_weights"])
# sort idf values
new_df_idf.sort_values(by=['idf_weights'], ascending=False)


idf_weights
aura                                           1.351237
papules                                        1.351237
weakness_in_limbs                              1.351237
vomiting                                       1.351237
visual_disturbances                            1.351237
unsteady_gait                                  1.351237
tremor                                         1.351237
throbbing_pain                                 1.351237
swelling_in_parotid_glands                     1.351237
slurred_speech                                 1.351237
shortness_of_breath                            1.351237
sensitivity_to_sound                           1.351237
sensitivity_to_light                           1.351237
redness                                        1.351237
pustules                                       1.351237
pain_while_swallowing                          1.351237
blurred_central_vision                         1.351237
pain_while_chewing                             1.351237
nausea                                         1.351237
muscle_weakness                                1.351237
lack_of_coordination                           1.351237
headache                                       1.351237
fever                                          1.351237
facial_paralysis                               1.351237
electric_shock_sensations_on_neck_movement     1.351237
dizziness                                      1.351237
difficulty_swallowing                          1.351237
difficulty_concentrating                       1.351237
whiteheads                                     1.351237
double_vision                                  1.240325
fatigue                                        1.153433

In [16]:
import pickle

with open('model.pkl', 'wb') as f:
    pickle.dump(knn_model, f)
    pickle.dump(cv, f)
    pickle.dump(new_cv, f) 
    pickle.dump(df_idf, f)
    pickle.dump(data, f)
    pickle.dump(all_symptoms, f)
    pickle.dump(input_symptoms, f)
    pickle.dump(input_age, f)
    pickle.dump(input_gender, f)
    pickle.dump(top_diseases, f)
    pickle.dump(indices, f)
    pickle.dump(distances, f)
    pickle.dump(k, f)
    pickle.dump(cols, f)
    pickle.dump(df, f)
    pickle.dump(docs, f)
    pickle.dump(word_count_vector, f)
    pickle.dump(tfidf_transformer, f)
    pickle.dump(new_word_count_vector, f) 
    pickle.dump(new_tfidf_transformer, f)  
    pickle.dump(input_vector, f)

print('Model saved successfully!')

Model saved successfully!
